# General instructions

The goal of the project is to materialize a set of **exploratory workloads** over a real-world, large-scale,  open-domain KG: [WikiData](https://www.wikidata.org/wiki/Wikidata:Main_Page)

An exploratory workload  is composed by a set of queries, where each query is related to the information obtained previously.

An exploratory workload starts with a usually vague, open ended question, and does not assume the person issuing the workload has a clear understanding of the data contained in the target database or its structure.

Remeber that:

1. All the queries must run in the python notebook
2. You can use classes and properties only if you find them via a SPARQL query that must be present in the notebook
3. You do not delete useless queries. Keep everything that is synthatically valid 

```
?p <http://schema.org/name> ?name .
```
    
is the BGP returning a human-readable name of a property or a class in Wikidata.
    
    

In [1]:
## SETUP used later

from SPARQLWrapper import SPARQLWrapper, JSON


prefixString = """
##-6ddde011ac-##
PREFIX wd: <http://www.wikidata.org/entity/> 
PREFIX wdt: <http://www.wikidata.org/prop/direct/> 
PREFIX sc: <http://schema.org/>
"""

# select and construct queries
def run_query(queryString):
    to_run = prefixString + "\n" + queryString

    sparql = SPARQLWrapper("http://a256-gc1-02.srv.aau.dk:5820/sparql")
    sparql.setTimeout(300)
    sparql.setReturnFormat(JSON)
    sparql.setQuery(to_run)

    try :
       results = sparql.query()
       json_results = results.convert()
       if len(json_results['results']['bindings'])==0:
          print("Empty")
          return 0
    
       for bindings in json_results['results']['bindings']:
          print( [ (var, value['value'])  for var, value in bindings.items() ] )

       return len(json_results['results']['bindings'])

    except Exception as e :
        print("The operation failed", e)
    
# ASk queries
def run_ask_query(queryString):
    to_run = prefixString + "\n" + queryString

    sparql = SPARQLWrapper("http://a256-gc1-03.srv.aau.dk:5820/sparql")
    sparql.setTimeout(300)
    sparql.setReturnFormat(JSON)
    sparql.setQuery(to_run)

    try :
        return sparql.query().convert()

    except Exception as e :
        print("The operation failed", e)


# GEO Workflow Series ("Place of Birth, Death, and Burial") 

Consider the following exploratory information need:

> You want to visit cities connected to famous writers and poets, and you are deciding wether to visit France or Germany

## Useful URIs for the current workflow


The following are given:

| IRI           | Description   | Role      |
| -----------   | -----------   |-----------|
| `wdt:P1647`   | subproperty   | predicate |
| `wdt:P31`     | instance of   | predicate |
| `wdt:P279`    | subclass      | predicate |
| `wdt:P106`    | occupation    | predicate |
| `wdt:P27`     | citizenship   | predicate |
| `wd:Q183`     | Germany       | node |
| `wd:Q142`     | France        | node |
| `wd:Q90`      | Paris         | node |
| `wd:Q49757`   | Poet          | node |
| `wd:Q36180`   | Writer        | node |
| `wd:Q501`     | Charles Baudelaire  | node      |
| `wd:Q272208`  | Montparnasse Cemetery       | node |


Also consider

```
?p wdt:P27 wd:Q142  . 
?p wdt:P106 wd:Q36180  . 
```

is the BGP to retrieve all **French writers**

## Workload Goals

1. Identify the BGP that connect people to their place of birth or place, death, or burial

2. Identify the BGP to obtain the country in which a place is located

3. How many poets and writers  have a place of birth, death, or burial in Germany and France?

4. Analyze cities across the two countries
 
   4.1 Is there any poet for which the birth place and the place of burial are located in the same city either in Germany or France?
   
   4.2 Which cities host the place of birth of the larger number of poets or writers across the two countries?
   
   4.3 What are the top 3 cities in each country that you could visit? Based on what criteria?


### Point 1 Start

In [3]:
# start your workflow here

In [2]:
queryString = """
SELECT COUNT(*)
WHERE { 

?p wdt:P27 wd:Q142  . 
?p wdt:P106 wd:Q36180  . 
} 
GROUP BY ?cult  ?arch
"""

print("Predicates")
run_query(queryString)

Predicates
[('callret-0', '14400')]


1

In [6]:
# Return all French writers
queryString = """
SELECT DISTINCT ?writer ?writerName
WHERE { 

    ?writer wdt:P27 wd:Q142. 
    ?writer wdt:P106 wd:Q36180. 
    ?writer <http://schema.org/name> ?writerName.
    
} 
ORDER BY ?writerName
"""

print("Predicates")
run_query(queryString)

Predicates
[('writer', 'http://www.wikidata.org/entity/Q18002932'), ('writerName', 'A. Augustin-Thierry')]
[('writer', 'http://www.wikidata.org/entity/Q28039087'), ('writerName', 'A. Des Tilleuls')]
[('writer', 'http://www.wikidata.org/entity/Q106837893'), ('writerName', 'A. Gennevraye')]
[('writer', 'http://www.wikidata.org/entity/Q18002264'), ('writerName', 'A. Verley')]
[('writer', 'http://www.wikidata.org/entity/Q43302265'), ('writerName', 'A.-Sébastien Kauffmann')]
[('writer', 'http://www.wikidata.org/entity/Q305864'), ('writerName', 'Abbas')]
[('writer', 'http://www.wikidata.org/entity/Q2622892'), ('writerName', 'Abbo Cernuus')]
[('writer', 'http://www.wikidata.org/entity/Q137934'), ('writerName', 'Abbot Suger')]
[('writer', 'http://www.wikidata.org/entity/Q23011391'), ('writerName', 'Abbé Alta')]
[('writer', 'http://www.wikidata.org/entity/Q17280159'), ('writerName', 'Abbé André')]
[('writer', 'http://www.wikidata.org/entity/Q1684952'), ('writerName', 'Abbé Aubert')]
[('writer',

14358

In [7]:
# Return all outgoing properties from French writers
queryString = """
SELECT DISTINCT ?property ?propertyName
WHERE { 

    ?writer wdt:P27 wd:Q142. 
    ?writer wdt:P106 wd:Q36180. 
    ?writer ?property ?object.
    ?property <http://schema.org/name> ?propertyName.
    
} 
ORDER BY ?propertyName
"""

print("Predicates")
run_query(queryString)

Predicates
[('property', 'http://www.wikidata.org/prop/direct/P8992'), ('propertyName', '1914-1918-Online ID')]
[('property', 'http://www.wikidata.org/prop/direct/P3314'), ('propertyName', '365chess player ID')]
[('property', 'http://www.wikidata.org/prop/direct/P9046'), ('propertyName', 'A*dS Encyclopedia ID')]
[('property', 'http://www.wikidata.org/prop/direct/P9634'), ('propertyName', 'AADFI member ID')]
[('property', 'http://www.wikidata.org/prop/direct/P8783'), ('propertyName', 'AAGM person or institution ID')]
[('property', 'http://www.wikidata.org/prop/direct/P6635'), ('propertyName', 'ACA author ID')]
[('property', 'http://www.wikidata.org/prop/direct/P3901'), ('propertyName', 'ADAGP artist ID')]
[('property', 'http://www.wikidata.org/prop/direct/P4114'), ('propertyName', 'ADK member ID')]
[('property', 'http://www.wikidata.org/prop/direct/P5463'), ('propertyName', 'AE member ID')]
[('property', 'http://www.wikidata.org/prop/direct/P2342'), ('propertyName', 'AGORHA person/insti

1512

In [10]:
# Return the place of birth, death and burial of Charles Baudelaire
queryString = """
SELECT DISTINCT ?propertyName ?place
WHERE { 

    wd:Q501 ?property ?place.
    ?property <http://schema.org/name> ?propertyName.
    FILTER(?property = wdt:P19 || ?property = wdt:P119 || ?property = wdt:P20)
    
    
} 
ORDER BY ?propertyName
"""

print("Predicates")
run_query(queryString)

Predicates
[('propertyName', 'place of birth'), ('place', 'http://www.wikidata.org/entity/Q90')]
[('propertyName', 'place of burial'), ('place', 'http://www.wikidata.org/entity/Q272208')]
[('propertyName', 'place of death'), ('place', 'http://www.wikidata.org/entity/Q90')]


3

In [15]:
# Identify the BGP that connect people to their place of birth or place, death, or burial
# Return the place of birth, death and burial of Charles Baudelaire
queryString = """
SELECT DISTINCT ?propertyName ?place ?placeName
WHERE { 

    wd:Q501 ?property ?place.
    ?place <http://schema.org/name> ?placeName.
    ?property <http://schema.org/name> ?propertyName.
    FILTER(?property = wdt:P19 || ?property = wdt:P119 || ?property = wdt:P20)
    
    
} 
ORDER BY ?propertyName
"""

print("Predicates")
run_query(queryString)

Predicates
[('propertyName', 'place of birth'), ('place', 'http://www.wikidata.org/entity/Q90'), ('placeName', 'Paris')]
[('propertyName', 'place of burial'), ('place', 'http://www.wikidata.org/entity/Q272208'), ('placeName', 'Montparnasse Cemetery')]
[('propertyName', 'place of death'), ('place', 'http://www.wikidata.org/entity/Q90'), ('placeName', 'Paris')]


3

### Point 1 End
DESCRIPTION: I started by testing the given relation by returning all French writers names. 
Then I returned all outgoing distinct properties from all French writers and discover all the relations I was interested in. 
I discover wdt:P495 “country of origin” that I decided to discard, but I kept wdt:P19 “place of birth”, wdt:P119 “place of burial” and wdt:P20 “place of death”.


RESULT: The result shows the BGP to return all interesting places for a specific person (Charles Baudelaire wdt:Q501 in this case)

### Point 2 Start

In [12]:
# Return all the outgoing properties of the places related to Charles Baudelaire
queryString = """
SELECT DISTINCT ?placeProperty ?placePropertyName
WHERE { 

    wd:Q501 ?property ?place.
    FILTER(?property = wdt:P19 || ?property = wdt:P119 || ?property = wdt:P20)
    
    ?place ?placeProperty ?object.
    ?placeProperty <http://schema.org/name> ?placePropertyName
    
    
} 
ORDER BY ?placeProperty
"""

print("Predicates")
run_query(queryString)

Predicates
[('placeProperty', 'http://www.wikidata.org/prop/direct/P1017'), ('placePropertyName', 'Vatican Library ID (former scheme)')]
[('placeProperty', 'http://www.wikidata.org/prop/direct/P1036'), ('placePropertyName', 'Dewey Decimal Classification')]
[('placeProperty', 'http://www.wikidata.org/prop/direct/P1082'), ('placePropertyName', 'population')]
[('placeProperty', 'http://www.wikidata.org/prop/direct/P1151'), ('placePropertyName', "topic's main Wikimedia portal")]
[('placeProperty', 'http://www.wikidata.org/prop/direct/P1225'), ('placePropertyName', 'U.S. National Archives Identifier')]
[('placeProperty', 'http://www.wikidata.org/prop/direct/P1245'), ('placePropertyName', 'OmegaWiki Defined Meaning')]
[('placeProperty', 'http://www.wikidata.org/prop/direct/P1296'), ('placePropertyName', 'Gran Enciclopèdia Catalana ID')]
[('placeProperty', 'http://www.wikidata.org/prop/direct/P131'), ('placePropertyName', 'located in the administrative territorial entity')]
[('placeProperty',

203

In [14]:
# Return the place of birth, death and burial with the country of Charles Baudelaire
queryString = """
SELECT DISTINCT ?propertyName ?place ?placeName ?country ?countryName
WHERE { 

    wd:Q501 ?property ?place.
    ?place <http://schema.org/name> ?placeName.
    ?property <http://schema.org/name> ?propertyName.
    FILTER(?property = wdt:P19 || ?property = wdt:P119 || ?property = wdt:P20)
    
    ?place wdt:P17 ?country.
    ?country <http://schema.org/name> ?countryName.
    
    
} 
ORDER BY ?propertyName
"""

print("Predicates")
run_query(queryString)

Predicates
[('propertyName', 'place of birth'), ('place', 'http://www.wikidata.org/entity/Q90'), ('placeName', 'Paris'), ('country', 'http://www.wikidata.org/entity/Q142'), ('countryName', 'France')]
[('propertyName', 'place of burial'), ('place', 'http://www.wikidata.org/entity/Q272208'), ('placeName', 'Montparnasse Cemetery'), ('country', 'http://www.wikidata.org/entity/Q142'), ('countryName', 'France')]
[('propertyName', 'place of death'), ('place', 'http://www.wikidata.org/entity/Q90'), ('placeName', 'Paris'), ('country', 'http://www.wikidata.org/entity/Q142'), ('countryName', 'France')]


3

In [16]:
# Identify the BGP to obtain the country in which a place is located
queryString = """
SELECT DISTINCT ?propertyName ?placeName ?countryName
WHERE { 

    wd:Q501 ?property ?place.
    ?place <http://schema.org/name> ?placeName.
    ?property <http://schema.org/name> ?propertyName.
    FILTER(?property = wdt:P19 || ?property = wdt:P119 || ?property = wdt:P20)
    
    ?place wdt:P17 ?country.
    ?country <http://schema.org/name> ?countryName.
    
    
} 
ORDER BY ?propertyName
"""

print("Predicates")
run_query(queryString)

Predicates
[('propertyName', 'place of birth'), ('placeName', 'Paris'), ('countryName', 'France')]
[('propertyName', 'place of burial'), ('placeName', 'Montparnasse Cemetery'), ('countryName', 'France')]
[('propertyName', 'place of death'), ('placeName', 'Paris'), ('countryName', 'France')]


3

### Point 2 End
DESCRIPTION: By considering Charles Baudelaire as I specific case I returned all the outgoing properties from the places related to him. I found the relations wdt:P17 “country” and wdt:131 ”located in administrative territorial”. At the end I kept the most obvious one wdt:P17.

RESULT: The result shows the requested BGP for a specific case. I returned the countries of all the interesting places (birth, death and burial) of Charles Baudelaire.

### Point 3 Start

In [2]:
# Return all poets and writers
queryString = """
SELECT DISTINCT ?personName ?profession
WHERE { 

    {
        ?person wdt:P106 wd:Q36180.
        ?person <http://schema.org/name> ?personName.
        wd:Q36180 <http://schema.org/name> ?profession
    }
    UNION
    {
        ?person wdt:P106 wd:Q49757.
        ?person <http://schema.org/name> ?personName.
        wd:Q49757 <http://schema.org/name> ?profession
    }
    
}
LIMIT 100
"""

print("Predicates")
run_query(queryString)

Predicates
[('personName', 'Youssef Ziedan'), ('profession', 'writer')]
[('personName', 'Eugénio de Castro'), ('profession', 'writer')]
[('personName', 'Amanda Palmer'), ('profession', 'writer')]
[('personName', 'Júlia Lopes de Almeida'), ('profession', 'writer')]
[('personName', 'Empress Xiaoquancheng'), ('profession', 'writer')]
[('personName', 'António Aleixo'), ('profession', 'writer')]
[('personName', 'Bohuslav Balbín'), ('profession', 'writer')]
[('personName', 'Aarão de Lacerda'), ('profession', 'writer')]
[('personName', 'Adelina Lopes Vieira'), ('profession', 'writer')]
[('personName', 'Amado Gómez Ugarte'), ('profession', 'writer')]
[('personName', 'Ana Vasco'), ('profession', 'writer')]
[('personName', 'Andrés García de Céspedes'), ('profession', 'writer')]
[('personName', 'Antoni Fabra i Ribas'), ('profession', 'writer')]
[('personName', 'Antoni Martí Monterde'), ('profession', 'writer')]
[('personName', 'Antonia Gutiérrez Bueno'), ('profession', 'writer')]
[('personName', 

100

In [8]:
# Return all poets and writers
queryString = """
SELECT DISTINCT ?personName ?profession
WHERE { 

    {
        ?person wdt:P106 wd:Q36180.
        ?person <http://schema.org/name> ?personName.
        ?e <http://schema.org/name> ?profession.
        FILTER (?e IN (wd:Q49757,wd:Q36180)).
    }

    
}
LIMIT 100
"""

print("Predicates")
run_query(queryString)

Predicates
[('personName', 'Youssef Ziedan'), ('profession', 'writer')]
[('personName', 'Eugénio de Castro'), ('profession', 'writer')]
[('personName', 'Amanda Palmer'), ('profession', 'writer')]
[('personName', 'Júlia Lopes de Almeida'), ('profession', 'writer')]
[('personName', 'Empress Xiaoquancheng'), ('profession', 'writer')]
[('personName', 'António Aleixo'), ('profession', 'writer')]
[('personName', 'Bohuslav Balbín'), ('profession', 'writer')]
[('personName', 'Aarão de Lacerda'), ('profession', 'writer')]
[('personName', 'Adelina Lopes Vieira'), ('profession', 'writer')]
[('personName', 'Amado Gómez Ugarte'), ('profession', 'writer')]
[('personName', 'Ana Vasco'), ('profession', 'writer')]
[('personName', 'Andrés García de Céspedes'), ('profession', 'writer')]
[('personName', 'Antoni Fabra i Ribas'), ('profession', 'writer')]
[('personName', 'Antoni Martí Monterde'), ('profession', 'writer')]
[('personName', 'Antonia Gutiérrez Bueno'), ('profession', 'writer')]
[('personName', 

100

In [2]:
# Return all poets and writers that have a place of birth, death or burial in France or Germany with the realive place
queryString = """
SELECT DISTINCT ?personName ?propertyName ?placeName ?countryName
WHERE { 

    {
        ?person wdt:P106 wd:Q36180.
        ?person <http://schema.org/name> ?personName.
        wd:Q36180 <http://schema.org/name> ?profession
    }
    UNION
    {
        ?person wdt:P106 wd:Q49757.
        ?person <http://schema.org/name> ?personName.
        wd:Q49757 <http://schema.org/name> ?profession
    }
    
    ?person ?property ?place.
    ?place <http://schema.org/name> ?placeName.
    ?property <http://schema.org/name> ?propertyName.
    FILTER(?property = wdt:P19 || ?property = wdt:P119 || ?property = wdt:P20)
    
    ?place wdt:P17 ?country.
    ?country <http://schema.org/name> ?countryName.
    FILTER(?country = wd:Q142 || ?country = wd:Q183)
}
ORDER BY ?personName
LIMIT 100
"""

print("Predicates")
run_query(queryString)

Predicates
[('personName', 'A. Augustin-Thierry'), ('propertyName', 'place of death'), ('placeName', 'Antibes'), ('countryName', 'France')]
[('personName', 'A. Augustin-Thierry'), ('propertyName', 'place of birth'), ('placeName', 'Lille'), ('countryName', 'France')]
[('personName', 'A. F. Koshko'), ('propertyName', 'place of death'), ('placeName', '16th arrondissement of Paris'), ('countryName', 'France')]
[('personName', 'A. Gennevraye'), ('propertyName', 'place of death'), ('placeName', 'Angers'), ('countryName', 'France')]
[('personName', 'A. Gennevraye'), ('propertyName', 'place of birth'), ('placeName', 'Baugé'), ('countryName', 'France')]
[('personName', 'A. I︠A︡blonovskīĭ'), ('propertyName', 'place of death'), ('placeName', 'Paris'), ('countryName', 'France')]
[('personName', 'A. Josef Štěpánek'), ('propertyName', 'place of death'), ('placeName', 'Dresden'), ('countryName', 'Germany')]
[('personName', 'A. M. W. Stirling'), ('propertyName', 'place of death'), ('placeName', 'Heide

100

In [8]:
# Return all distinct poets and writers that have a place of birth, death or burial in France or Germany
queryString = """
SELECT DISTINCT ?person ?personName ?countryName
WHERE { 

    {
        ?person wdt:P106 wd:Q36180.
        ?person <http://schema.org/name> ?personName.
        wd:Q36180 <http://schema.org/name> ?profession
    }
    UNION
    {
        ?person wdt:P106 wd:Q49757.
        ?person <http://schema.org/name> ?personName.
        wd:Q49757 <http://schema.org/name> ?profession
    }
    
    ?person ?property ?place.
    ?place <http://schema.org/name> ?placeName.
    ?property <http://schema.org/name> ?propertyName.
    FILTER(?property = wdt:P19 || ?property = wdt:P119 || ?property = wdt:P20)
    
    ?place wdt:P17 ?country.
    ?country <http://schema.org/name> ?countryName.
    FILTER(?country = wd:Q142 || ?country = wd:Q183)
}
ORDER BY ?personName
"""

print("Predicates")
run_query(queryString)

Predicates
[('person', 'http://www.wikidata.org/entity/Q18002932'), ('personName', 'A. Augustin-Thierry'), ('countryName', 'France')]
[('person', 'http://www.wikidata.org/entity/Q4237101'), ('personName', 'A. F. Koshko'), ('countryName', 'France')]
[('person', 'http://www.wikidata.org/entity/Q60458976'), ('personName', 'A. Gennevraye'), ('countryName', 'France')]
[('person', 'http://www.wikidata.org/entity/Q12173237'), ('personName', 'A. I︠A︡blonovskīĭ'), ('countryName', 'France')]
[('person', 'http://www.wikidata.org/entity/Q95371681'), ('personName', 'A. Josef Štěpánek'), ('countryName', 'Germany')]
[('person', 'http://www.wikidata.org/entity/Q4648153'), ('personName', 'A. M. W. Stirling'), ('countryName', 'Germany')]
[('person', 'http://www.wikidata.org/entity/Q4323581'), ('personName', 'A. O. Osipovich-Novodvorskiĭ'), ('countryName', 'France')]
[('person', 'http://www.wikidata.org/entity/Q4393257'), ('personName', 'A. Rennikov'), ('countryName', 'France')]
[('person', 'http://www.w

42744

In [9]:
# Return all distinct poets and writers that have a place of birth, death or burial in France or Germany
queryString = """
SELECT DISTINCT ?person ?personName ?countryName
WHERE { 

    {
        ?person wdt:P106 wd:Q36180.
        ?person <http://schema.org/name> ?personName.
        wd:Q36180 <http://schema.org/name> ?profession
    }
    UNION
    {
        ?person wdt:P106 wd:Q49757.
        ?person <http://schema.org/name> ?personName.
        wd:Q49757 <http://schema.org/name> ?profession
    }
    
    ?person ?property ?place.
    ?place <http://schema.org/name> ?placeName.
    ?property <http://schema.org/name> ?propertyName.
    FILTER(?property = wdt:P19 || ?property = wdt:P119 || ?property = wdt:P20)
    
    ?place wdt:P17 wd:Q142.
    ?place wdt:P17 wd:Q183.
}
ORDER BY ?personName
"""

print("Predicates")
run_query(queryString)

Predicates
[('person', 'http://www.wikidata.org/entity/Q2263241'), ('personName', 'Aurelianus of Arles')]
[('person', 'http://www.wikidata.org/entity/Q899826'), ('personName', 'Cyprianus')]
[('person', 'http://www.wikidata.org/entity/Q662458'), ('personName', 'Eucheria')]
[('person', 'http://www.wikidata.org/entity/Q4485272'), ('personName', 'Flavius Felix')]
[('person', 'http://www.wikidata.org/entity/Q3207287'), ('personName', 'Gaius Julius Victor')]
[('person', 'http://www.wikidata.org/entity/Q373675'), ('personName', 'Gennadius of Massilia')]
[('person', 'http://www.wikidata.org/entity/Q43977'), ('personName', 'Jan Hus')]
[('person', 'http://www.wikidata.org/entity/Q209102'), ('personName', 'Lactantius')]
[('person', 'http://www.wikidata.org/entity/Q2891791'), ('personName', 'Pacatus Drepanius')]
[('person', 'http://www.wikidata.org/entity/Q705919'), ('personName', 'Rutilius Claudius Namatianus')]
[('person', 'http://www.wikidata.org/entity/Q662111'), ('personName', 'Severus Sanctu

13

In [3]:
# How many poets and writers have a place of birth, death, or burial in Germany and France?
queryString = """
SELECT ?countryName (COUNT(DISTINCT ?person) AS ?count)
WHERE { 

    {
        ?person wdt:P106 wd:Q36180.
        ?person <http://schema.org/name> ?personName.
        wd:Q36180 <http://schema.org/name> ?profession
    }
    UNION
    {
        ?person wdt:P106 wd:Q49757.
        ?person <http://schema.org/name> ?personName.
        wd:Q49757 <http://schema.org/name> ?profession
    }
    
    ?person ?property ?place.
    ?place <http://schema.org/name> ?placeName.
    ?property <http://schema.org/name> ?propertyName.
    FILTER(?property = wdt:P19 || ?property = wdt:P119 || ?property = wdt:P20)
    
    ?place wdt:P17 ?country.
    ?country <http://schema.org/name> ?countryName.
    FILTER(?country = wd:Q142 || ?country = wd:Q183)
}
ORDER BY ?countryName
"""

print("Predicates")
run_query(queryString)

Predicates
[('countryName', 'France'), ('count', '15818')]
[('countryName', 'Germany'), ('count', '26926')]


2

### Point 3 End
DESCRIPTION: I started by returning the first poets and writes in the database. 
Then I returned all the poets and writers that have at least one interesting place located in “France” wd:Q142 or “Germany” wd:Q183.
Then I repeated the query but keeping only one record for a person. So, If a person has more than one interesting place in France or Germany it will be counted only one time.
The last query counts the distinct poets that have an interesting place in France or Germany. 


RESULT: The result shows how many poets and writers have an interesting place in Germany or in France.
We can observe that Germany won with 26926 people. People with interesting places in both Germany and France are counted for both countries.


### Point 4.1 Start

In [5]:
# Is there any poet for which the birth place and the place of burial are located in the same city either in Germany or France? 
queryString = """
SELECT DISTINCT ?personName ?placeName ?countryName
WHERE { 

    ?person wdt:P106 wd:Q49757.
    ?person <http://schema.org/name> ?personName.


    ?person wdt:P19 ?birthPlace.
    ?person wdt:P119 ?burialPlace.
    ?birthPlace <http://schema.org/name> ?placeName.
    FILTER(?birthPlace = ?burialPlace)
    
    
    ?birthPlace wdt:P17 ?country.
    ?country <http://schema.org/name> ?countryName.
    FILTER(?country = wd:Q142 || ?country = wd:Q183)
}
ORDER BY ?personName
"""

print("Predicates")
run_query(queryString)

Predicates
[('personName', 'Alphonse Germain-Lacour'), ('placeName', 'Moulins-sur-Orne'), ('countryName', 'France')]
[('personName', 'Boris Vian'), ('placeName', "Ville-d'Avray"), ('countryName', 'France')]
[('personName', 'Charles Bécas'), ('placeName', 'Ainhoa'), ('countryName', 'France')]
[('personName', 'Charles-Louis Philippe'), ('placeName', 'Cérilly'), ('countryName', 'France')]
[('personName', 'Ernest Louis, Grand Duke of Hesse'), ('placeName', 'Darmstadt'), ('countryName', 'Germany')]
[('personName', 'Erwan ar Moal'), ('placeName', 'Coadout'), ('countryName', 'France')]
[('personName', 'Eugène Bizeau'), ('placeName', 'Véretz'), ('countryName', 'France')]
[('personName', 'Gaston Bachelard'), ('placeName', 'Bar-sur-Aube'), ('countryName', 'France')]
[('personName', 'Gisèle Barbotin'), ('placeName', 'Argenton-sur-Creuse'), ('countryName', 'France')]
[('personName', "Jules Amédée Barbey d'Aurevilly"), ('placeName', 'Saint-Sauveur-le-Vicomte'), ('countryName', 'France')]
[('personN

22

### Point 4.1 End
DESCRIPTION: This query was obtained by simply use a filter and impose the equivalence between the burial and the birthplace.


RESULT: The result shows 22 poets with same burial and birthplace. 

### Point 4.2 Start

In [8]:
# Return the French cities with the count of the birth of Poets and Writers
queryString = """
SELECT DISTINCT ?placeName (COUNT(?person) AS ?numberOfBirth)
WHERE { 

    {
        ?person wdt:P106 wd:Q36180.
    }
    UNION
    {
        ?person wdt:P106 wd:Q49757.
    }
    
    ?person wdt:P19 ?place.
    ?place <http://schema.org/name> ?placeName.
    
    ?place wdt:P17 wd:Q142.
}
ORDER BY DESC (?numberOfBirth)
"""

print("Predicates")
run_query(queryString)

Predicates
[('placeName', 'Paris'), ('numberOfBirth', '2792')]
[('placeName', 'Marseille'), ('numberOfBirth', '290')]
[('placeName', 'Lyon'), ('numberOfBirth', '288')]
[('placeName', 'Strasbourg'), ('numberOfBirth', '206')]
[('placeName', 'Bordeaux'), ('numberOfBirth', '198')]
[('placeName', 'Toulouse'), ('numberOfBirth', '148')]
[('placeName', 'Rouen'), ('numberOfBirth', '136')]
[('placeName', 'Nantes'), ('numberOfBirth', '126')]
[('placeName', 'Neuilly-sur-Seine'), ('numberOfBirth', '123')]
[('placeName', 'Nîmes'), ('numberOfBirth', '110')]
[('placeName', 'France'), ('numberOfBirth', '109')]
[('placeName', 'Lille'), ('numberOfBirth', '104')]
[('placeName', 'Boulogne-Billancourt'), ('numberOfBirth', '97')]
[('placeName', 'Nice'), ('numberOfBirth', '94')]
[('placeName', 'Nancy'), ('numberOfBirth', '90')]
[('placeName', 'Montpellier'), ('numberOfBirth', '81')]
[('placeName', 'Dijon'), ('numberOfBirth', '79')]
[('placeName', 'Versailles'), ('numberOfBirth', '74')]
[('placeName', 'Metz'),

3077

In [17]:
# Which cities host the place of birth of the larger number of poets or writers across the two countries?
queryString = """
SELECT DISTINCT ?countryName ?placeName ?numberOfBirth
WHERE {

    {
        SELECT DISTINCT ?countryName ?placeName (COUNT(?person) AS ?numberOfBirth) 
        WHERE { 

            {
                ?person wdt:P106 wd:Q36180.
            }
            UNION
            {
                ?person wdt:P106 wd:Q49757.
            }

            ?person wdt:P19 ?place.
            ?place <http://schema.org/name> ?placeName.

            ?place wdt:P17 wd:Q142.
            wd:Q142 <http://schema.org/name> ?countryName.
        }
        ORDER BY DESC (?numberOfBirth)
        LIMIT 1
    }
    UNION
    {
        SELECT DISTINCT ?countryName ?placeName (COUNT(?person) AS ?numberOfBirth) 
        WHERE { 

            {
                ?person wdt:P106 wd:Q36180.
            }
            UNION
            {
                ?person wdt:P106 wd:Q49757.
            }

            ?person wdt:P19 ?place.
            ?place <http://schema.org/name> ?placeName.

            ?place wdt:P17 wd:Q183.
            wd:Q183 <http://schema.org/name> ?countryName.
        }
        ORDER BY DESC (?numberOfBirth)
        LIMIT 1
    }
}
"""

print("Predicates")
run_query(queryString)

Predicates
[('countryName', 'France'), ('placeName', 'Paris'), ('numberOfBirth', '2792')]
[('countryName', 'Germany'), ('placeName', 'Berlin'), ('numberOfBirth', '2015')]


2

### Point 4.2 End
DESCRIPTION: I tested the query considering only places in France. So, I counted how many poets and writers have the birthplace in a city of France.
The second query does the same as previous but with both countries and keeping only the cities with higher count. One per country.


RESULT: Of course, the cities are the capital of the countries. Paris won with 2792 people.

### Point 4.3 Start

In [19]:
# Return the French cities with the count of the birth, death and buries places of Poets and Writers
queryString = """
SELECT DISTINCT ?placeName (COUNT(?person) AS ?interestScore)
WHERE { 

    {
        ?person wdt:P106 wd:Q36180.
    }
    UNION
    {
        ?person wdt:P106 wd:Q49757.
    }
    
    ?person ?property ?place.
    ?place <http://schema.org/name> ?placeName.
    FILTER(?property = wdt:P19 || ?property = wdt:P119 || ?property = wdt:P20)
    
    ?place wdt:P17 wd:Q142.
}
ORDER BY DESC (?interestScore)
"""

print("Predicates")
run_query(queryString)

Predicates
[('placeName', 'Paris'), ('interestScore', '6810')]
[('placeName', 'Père Lachaise Cemetery'), ('interestScore', '693')]
[('placeName', 'Marseille'), ('interestScore', '425')]
[('placeName', 'Lyon'), ('interestScore', '377')]
[('placeName', 'Strasbourg'), ('interestScore', '307')]
[('placeName', 'Neuilly-sur-Seine'), ('interestScore', '267')]
[('placeName', 'Bordeaux'), ('interestScore', '260')]
[('placeName', 'Nice'), ('interestScore', '260')]
[('placeName', 'Montparnasse Cemetery'), ('interestScore', '237')]
[('placeName', 'Toulouse'), ('interestScore', '218')]
[('placeName', 'France'), ('interestScore', '178')]
[('placeName', 'Nantes'), ('interestScore', '173')]
[('placeName', 'Rouen'), ('interestScore', '171')]
[('placeName', '14th arrondissement of Paris'), ('interestScore', '163')]
[('placeName', '16th arrondissement of Paris'), ('interestScore', '161')]
[('placeName', 'Nîmes'), ('interestScore', '154')]
[('placeName', 'Versailles'), ('interestScore', '152')]
[('placeNa

4404

In [23]:
# Return the interest score of cities related to Charles Baudelaire
queryString = """
SELECT DISTINCT ?placeName (COUNT(wd:Q501) AS ?interestScore)
WHERE { 
    
    wd:Q501 ?property ?place.
    ?place <http://schema.org/name> ?placeName.
    FILTER(?property = wdt:P19 || ?property = wdt:P119 || ?property = wdt:P20)
    
    ?place wdt:P17 wd:Q142.
}
ORDER BY DESC (?interestScore)
"""

print("Predicates")
run_query(queryString)

Predicates
[('placeName', 'Paris'), ('interestScore', '2')]
[('placeName', 'Montparnasse Cemetery'), ('interestScore', '1')]


2

In [25]:
# Return the French cities interestScore
queryString = """
SELECT DISTINCT ?placeName (COUNT(?property) AS ?interestScore)
WHERE { 

    {
        ?person wdt:P106 wd:Q36180.
    }
    UNION
    {
        ?person wdt:P106 wd:Q49757.
    }
    
    ?person ?property ?place.
    ?place <http://schema.org/name> ?placeName.
    FILTER(?property = wdt:P19 || ?property = wdt:P119 || ?property = wdt:P20)
    
    ?place wdt:P17 wd:Q142.
}
ORDER BY DESC (?interestScore)
"""

print("Predicates")
run_query(queryString)

Predicates
[('placeName', 'Paris'), ('interestScore', '6810')]
[('placeName', 'Père Lachaise Cemetery'), ('interestScore', '693')]
[('placeName', 'Marseille'), ('interestScore', '425')]
[('placeName', 'Lyon'), ('interestScore', '377')]
[('placeName', 'Strasbourg'), ('interestScore', '307')]
[('placeName', 'Neuilly-sur-Seine'), ('interestScore', '267')]
[('placeName', 'Bordeaux'), ('interestScore', '260')]
[('placeName', 'Nice'), ('interestScore', '260')]
[('placeName', 'Montparnasse Cemetery'), ('interestScore', '237')]
[('placeName', 'Toulouse'), ('interestScore', '218')]
[('placeName', 'France'), ('interestScore', '178')]
[('placeName', 'Nantes'), ('interestScore', '173')]
[('placeName', 'Rouen'), ('interestScore', '171')]
[('placeName', '14th arrondissement of Paris'), ('interestScore', '163')]
[('placeName', '16th arrondissement of Paris'), ('interestScore', '161')]
[('placeName', 'Nîmes'), ('interestScore', '154')]
[('placeName', 'Versailles'), ('interestScore', '152')]
[('placeNa

4404

In [28]:
# Return the Germany cities interestScore
queryString = """
SELECT DISTINCT ?placeName (COUNT(?property) AS ?interestScore)
WHERE { 

    {
        ?person wdt:P106 wd:Q36180.
    }
    UNION
    {
        ?person wdt:P106 wd:Q49757.
    }
    
    ?person ?property ?place.
    ?place <http://schema.org/name> ?placeName.
    FILTER(?property = wdt:P19 || ?property = wdt:P119 || ?property = wdt:P20)
    
    ?place wdt:P17 wd:Q183.
}
ORDER BY DESC (?interestScore)
"""

print("Predicates")
run_query(queryString)

Predicates
[('placeName', 'Berlin'), ('interestScore', '3768')]
[('placeName', 'Munich'), ('interestScore', '1713')]
[('placeName', 'Hamburg'), ('interestScore', '1408')]
[('placeName', 'Leipzig'), ('interestScore', '856')]
[('placeName', 'Dresden'), ('interestScore', '720')]
[('placeName', 'Frankfurt am Main'), ('interestScore', '704')]
[('placeName', 'Cologne'), ('interestScore', '681')]
[('placeName', 'Stuttgart'), ('interestScore', '651')]
[('placeName', 'Hanover'), ('interestScore', '484')]
[('placeName', 'Düsseldorf'), ('interestScore', '387')]
[('placeName', 'Nuremberg'), ('interestScore', '382')]
[('placeName', 'Bonn'), ('interestScore', '299')]
[('placeName', 'Freiburg im Breisgau'), ('interestScore', '265')]
[('placeName', 'Brunswick'), ('interestScore', '265')]
[('placeName', 'Halle (Saale)'), ('interestScore', '262')]
[('placeName', 'Bremen'), ('interestScore', '251')]
[('placeName', 'Heidelberg'), ('interestScore', '249')]
[('placeName', 'Lübeck'), ('interestScore', '244')

5451

In [27]:
#  What are the top 3 cities in each country that you could visit? Based on what criteria?
# I will visit the cities with more birth, death and burial places 
queryString = """
SELECT ?countryName ?placeName ?interestScore
WHERE {

    {
        SELECT DISTINCT ?countryName ?placeName (COUNT(?property) AS ?interestScore)
        WHERE { 

            {
                ?person wdt:P106 wd:Q36180.
            }
            UNION
            {
                ?person wdt:P106 wd:Q49757.
            }

            ?person ?property ?place.
            ?place <http://schema.org/name> ?placeName.
            FILTER(?property = wdt:P19 || ?property = wdt:P119 || ?property = wdt:P20)

            ?place wdt:P17 wd:Q142.
            wd:Q142 <http://schema.org/name> ?countryName.
        }
        ORDER BY DESC (?interestScore)
        LIMIT 3
    }
    UNION
    {
        SELECT DISTINCT ?countryName ?placeName (COUNT(?property) AS ?interestScore)
        WHERE { 

            {
                ?person wdt:P106 wd:Q36180.
            }
            UNION
            {
                ?person wdt:P106 wd:Q49757.
            }

            ?person ?property ?place.
            ?place <http://schema.org/name> ?placeName.
            FILTER(?property = wdt:P19 || ?property = wdt:P119 || ?property = wdt:P20)

            ?place wdt:P17 wd:Q183.
            wd:Q183 <http://schema.org/name> ?countryName.
        }
        ORDER BY DESC (?interestScore)
        LIMIT 3
    }

}


"""

print("Predicates")
run_query(queryString)

Predicates
[('countryName', 'France'), ('placeName', 'Paris'), ('interestScore', '6810')]
[('countryName', 'France'), ('placeName', 'Père Lachaise Cemetery'), ('interestScore', '693')]
[('countryName', 'France'), ('placeName', 'Marseille'), ('interestScore', '425')]
[('countryName', 'Germany'), ('placeName', 'Berlin'), ('interestScore', '3768')]
[('countryName', 'Germany'), ('placeName', 'Munich'), ('interestScore', '1713')]
[('countryName', 'Germany'), ('placeName', 'Hamburg'), ('interestScore', '1408')]


6

### Point 4.3 End
DESCRIPTION: For every city I compute the interestingScore. This score counts how many people have an interesting place in that city. The more the places to visit the higher is the interestingScore.
So, I tested this for places in France and then for Charles Baudelaire. I this way I was sure that Charles Baudelaire counts two times for Paris and one time for Montparnasse Cemetery.
Then I computed the same for cities in Germany.
The last query combines the above results by keeping only the most 3 interesting places per country.


RESULT: The result shows that the most interesting place in absolute is Paris with a score of 6810. 
But we can see that Germany has more cities that are very interesting while France has only Paris.